In [71]:
import jax
import optax
import flax
import jax.numpy as jnp
import datasets
from flax.training import train_state
from flax.training.common_utils import get_metrics, onehot, shard
from datasets import load_dataset
from tokenizers import trainers, Tokenizer, normalizers, ByteLevelBPETokenizer
from pathlib import Path
import numpy as np
import transformers
from tqdm.notebook import tqdm
from pathlib import Path
from transformers import AutoConfig
from typing import Dict, List, Optional, Tuple
from transformers import AutoTokenizer
from transformers import PreTrainedTokenizerBase
from transformers import FlaxAutoModelForMaskedLM
from dataclasses import dataclass, field
import time
import glob
import random

In [72]:
from transformers import AutoConfig


In [74]:
from transformers import AutoTokenizer

In [75]:
tokenizer = AutoTokenizer.from_pretrained("./")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [81]:
tokenizer.vocab_size

36450

In [3]:


config = AutoConfig.from_pretrained("google/bigbird-roberta-base")

In [4]:
config.save_pretrained("./")

In [60]:
len([x for x in data_files if isinstance(x, str)])

2848

In [61]:
data_files

['/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00943-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00018-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-01012-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00625-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00070-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00108-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00315-of-01024.json.gz',
 '/data/nrc_uniq_cleaned_20210223/part-00056-47c217ad-de48-4b5e-b177-ef4bcd69ad2b-c000.json.gz',
 '/data/nrc_uniq_cleaned_20210223/part-00140-47c217ad-de48-4b5e-b177-ef4bcd69ad2b-c000.json.gz',
 '/data/nu_uniq_cleaned_20210225/part-00128-f31777cc-bf2a-4d2c-95c8-22f5eec50039-c000.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00221-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00394-of-01024.json.gz',
 '/data/c4_cleaned2/cleaned2_c4-nl.tfrecord-00469-of-01024.json.gz',
 '/data/c4_cleaned2/

In [45]:
    datafiles = []
    import glob
    import random
    SEED = 12345
    def add_jsonlines_dir(path, filespec):
        global data_files
        data_files += glob.glob(f"{path}/{filespec}")
        data_files = list(set(data_files))
        print(f"Number of files {len(data_files)} after adding {path} glob {filespec}")
    add_jsonlines_dir(f"/data/c4_cleaned2", "*.gz")
    add_jsonlines_dir(f"/data/nrc_uniq_cleaned_20210223", "*.gz")
    add_jsonlines_dir(f"/data/nu_uniq_cleaned_20210225", "*.gz")
    datafiles

Number of files 2448 after adding /data/c4_cleaned2 glob *.gz
Number of files 2648 after adding /data/nrc_uniq_cleaned_20210223 glob *.gz
Number of files 2848 after adding /data/nu_uniq_cleaned_20210225 glob *.gz


[]

In [38]:
train_val_files()

Number of files 1424 after adding /data/c4_cleaned2 glob *.gz
Number of files 1424 after adding /data/nrc_uniq_cleaned_20210223 glob *.gz
Number of files 1424 after adding /data/nu_uniq_cleaned_20210225 glob *.gz


In [ ]:
    random.Random(SEED).shuffle(data_files)
    total = len(data_files)
    print(total)
    perc = 0.05
    val_size = int(perc * total)
    train_size = total - val_size
    train = data_files[:train_size]
    val = data_files[train_size:]
    print(f"Got {len(train)} training files and {perc*100} % {len(val)} validation files")
    assert list(set(train) & set(val)) == [], "Train overlaps with test"
    return train, val

In [ ]:
    datafiles = []
    import glob
    import random
    SEED = 12345
    def add_jsonlines_dir(path, filespec):
        global data_files
        data_files += glob.glob(f"{path}/{filespec}")
        data_files = list(set(data_files))
        print(f"Number of files {len(data_files)} after adding {path} glob {filespec}")
    add_jsonlines_dir(f"/data/c4_cleaned2", "*.gz")
    add_jsonlines_dir(f"/data/nrc_uniq_cleaned_20210223", "*.gz")
    add_jsonlines_dir(f"/data/nu_uniq_cleaned_20210225", "*.gz")

In [ ]:
datasets["train"] = load_dataset(datafiles, split="train[5%:]")
datasets["validation"] = load_dataset(datafiles, split="train[5%:]")

In [34]:
train, val = train_val_files()
datasets = load_dataset('json', data_files={'train': train, 'validation': val})

Number of files 1424 after adding /data/c4_cleaned2 glob *.gz
Number of files 1424 after adding /data/nrc_uniq_cleaned_20210223 glob *.gz
Number of files 1424 after adding /data/nu_uniq_cleaned_20210225 glob *.gz
1424
Got 1353 training files and 5.0 % 71 validation files


0 tables [00:00, ? tables/s]

JSONDecodeError: Extra data: line 2 column 1 (char 651)

In [70]:
import glob
import random
SEED = 12345
data_files = []
def add_jsonlines_dir(path, filespec):
    global data_files
    data_files += glob.glob(f"{path}/{filespec}")
    data_files = list(set(data_files))
    print(f"Number of files {len(data_files)} after adding {path} glob {filespec}")
add_jsonlines_dir(f"/data/c4_cleaned2", "*json.gz")
add_jsonlines_dir(f"/data/nrc_uniq_cleaned_20210223", "*.gz")
add_jsonlines_dir(f"/data/nu_uniq_cleaned_20210225", "*.gz")

Number of files 1024 after adding /data/c4_cleaned2 glob *json.gz
Number of files 1224 after adding /data/nrc_uniq_cleaned_20210223 glob *.gz
Number of files 1424 after adding /data/nu_uniq_cleaned_20210225 glob *.gz


In [29]:
datasets = load_dataset('json', data_files={'train': train, 'validation': val})

In [21]:
dataset_iterator = iter(datasets['train'])

In [22]:
print(next(dataset_iterator))

{'text': 'Welke school kiezen?\nSchoolinformatie in je brievenbus ... graag of liever niet?\nKinderen die geboren zijn tussen 15 november en 31 december 2016 stappen pas in op 1 september 2019.\nVoor deze groep is inschrijving mogelijk tijdens de eerste voorrangsperiode: van 1 maart tot 16 maart 2018.\n2: kinderen van personeel van de school.\nVoor deze groep is inschrijving mogelijk tijdens de tweede voorrangsperiode: op 22 maart en 23 maart 2018.\nVanaf 18 april tot 4mei 2018 loopt de algemene inschrijvingsperiode en dan kunnen alle kinderen ingeschreven worden.\nTIP: Wacht niet tot de laatste dag om je kind in te schrijven. Hoe sneller je inschrijft, hoe groter de kans dat er plaats is in de school die je kiest.\nKies bij voorkeur een school in de buurt van waar je woont; dat heeft enkel maar voordelen. Bezoek zeker vooraf de school van je keuze. Je kan er uitleg vragen en de schoolomgeving ontdekken.\nIn welke school zijn er vrije plaatsen?\nVanaf 30 maart 2018 vanaf 17u vind je in

In [13]:
#59G c4_cleaned compressed
#937M nrc_uniq_cleaned_20210223 compressed
#410M nu_uniq_cleaned_20210225 compressed
#9.9G oscar_nl_cleaned compressed



data_files = []
SEED=42
def add_jsonlines_dir(path,filespec):
    global data_files
    data_files += glob.glob(f"{path}/{filespec}")
    print(f"Number of files {len(data_files)} after adding {path}")
    
#add_jsonlines_dir("/home/dat/subset_c4_cleannl","*.gz")   
add_jsonlines_dir("/data/oscar_nl_cleaned2","*.gz")
#add_jsonlines_dir("/data/nrc_cleaned_idtextfmt","*.gz")
#add_jsonlines_dir("/data/nu_cleaned_idtextfmt","*.gz")

add_jsonlines_dir(f"{data_dir}/c4_cleaned", "*73*.gz")

    
random.Random(SEED).shuffle(data_files)
total = len(data_files)
val_size = int(0.05 * total)
train_size = total - val_size
print(f"95%: {train_size}")
train = data_files[:train_size]
val = data_files[train_size:]
print(f"Got {len(train)} training files and {len(val)} validation files")
assert list(set(train) & set(val)) == [], "Train overlaps with test"
datasets = load_dataset('json', data_files={'train': train, 'validation': val})


assert list(set(train) & set(val)) == [], 'train overlaps with test'


Number of files 0 after adding /data/oscar_nl_cleaned2


NameError: name 'data_dir' is not defined

In [ ]:
from datasets import Dataset
datasets['train'] = Dataset.from_file("/home/dat/.cache/huggingface/datasets/json/default-3eb349358dcf6436/0.0.0/f92a4de297ac644ad9781979b79064b0e222b3af766f8ea3bee32390dca23723/json-train.arrow") 
datasets['validation'] = Dataset.from_file("/home/dat/.cache/huggingface/datasets/json/default-3eb349358dcf6436/0.0.0/f92a4de297ac644ad9781979b79064b0e222b3af766f8ea3bee32390dca23723/json-validation.arrow") 



In [41]:
dataset_iterator = iter(datasets['train'])

In [78]:
print(next(dataset_iterator)['text'])

Zo stel ik het me voor. Tegen iedere conventie in. Och wat heeft de burgerij gemopperd en schande gesproken. Dat was in die dagen. Nu nog steeds, maar anders. Daarover later meer. En wat zullen ze van u gehouden hebben in de kleine kring van liefhebbers.
Jaren geleden, toen ik nog op de academie zat bestudeerde ik uw werk. Vooral de paar overgebleven foto’s van uw Merzbau in Hannover troffen mij. Zo vrij en swingend en onconventioneel.
Ze werden opgeslagen in een afgelegen kamer in mijn geheugen, want eigentijdse choreografen en filmmakers en schilders uit de vroege renaissance vroegen om voorrang.
Toen u het huis van uw ouders in Hannover betrok transformeerde u acht kamers tot een betoverende sculptuur. Merzbau! Kathedrale des erotischen Elend.
In abstracte vlakken en vormen kruipen de volumes chaotisch omhoog langs de muren. Meestal wit. Er vormen zich ruimtes en grotachtige structuren. Hier en daar een typografisch detail of een herkenbaar object, dat uit zijn context geslingerd, v

In [31]:

            add_jsonlines_dir("/home/dat/subset_c4_cleannl")   
            add_jsonlines_dir("/data/oscar_nl_cleaned")
            add_jsonlines_dir("/data/nrc_cleaned_idtextfmt")
            add_jsonlines_dir("/data/nu_cleaned_idtextfmt")
            random.Random(SEED).shuffle(data_files)
            total = len(data_files)
            val_size = int(0.05 * total)
            train_size = total - val_size
            print(f"95%: {train_size}")
            train = data_files
            val = data_files
            print(f"Got {len(train)} training files and {len(val)} validation files")
            assert list(set(train) & set(val)) == [], "Train overlaps with test"
            return train, val
        train, val = train_val_files()
        datasets = load_dataset('json', data_files={'train': train, 'validation': val})

IndentationError: unexpected indent (1021262509.py, line 15)

In [4]:
from tokenizers import ByteLevelBPETokenizer
tokenizer = ByteLevelBPETokenizer()

def batch_iterator(batch_size=1000):
    for i in range(0, len(datasets), batch_size):
        yield datasets["train"][i: i + batch_size]["text"]

tokenizer.train_from_iterator(batch_iterator(), vocab_size=50358, min_frequency=2, special_tokens=[
    "<s>",
    "<pad>",
    "</s>",
    "<unk>",
    "<mask>",
])

In [5]:
tokenizer.get_vocab_size()

39503

In [6]:
cd ~/pino-roberta-base

/home/dat/pino-roberta-base


In [7]:
tokenizer.save("tokenizer.json")

In [ ]:
dataset1 = load_dataset("mc4", "nl", streaming=True)
dataset2 = load_dataset("oscar", "unshuffled_deduplicated_nl",streaming=True)
dataset3 = load_dataset("cc100", lang="nl")



Using custom data configuration nl-lang=nl


Downloading:   0%|          | 0.00/8.42G [00:00<?, ?B/s]

In [14]:
from transformers import AutoTokenizer, RobertaModel
from transformers import BigBirdForSequenceClassification,FlaxBigBirdModel,FlaxBigBirdForMaskedLM

model = FlaxBigBirdModel.from_pretrained("flax-community/pino-roberta-base")
model.save_pretrained('exported_pytorch_model')

INFO:absl:Starting the local TPU driver.
INFO:absl:Unable to initialize backend 'tpu_driver': Not found: Unable to find driver in registry given worker: local://
INFO:absl:Unable to initialize backend 'gpu': Not found: Could not find registered platform with name: "cuda". Available platform names are: Interpreter Host TPU
Some weights of FlaxBigBirdModel were not initialized from the model checkpoint at flax-community/pino-roberta-base and are newly initialized: {('pooler', 'kernel'), ('pooler', 'bias')}
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
